# Use Detectron2 v0.4 

This notebook serves two purposes, the first purpose is to check the best.ckpt that was given by the owner of the project,
The second purpose is to freeze the backbone layers and compare the model that loads best.ckpt and the model that loads the checkpoint that has been frozen and tested on the some data images.

In [1]:
import numpy as np
import torch
import torch.nn as nn
import torch.nn.functional as F
from detectron2.config import get_cfg
from detectron2 import model_zoo
from detectron2.modeling import build_model
from detectron2.utils.events import EventStorage
from detectron2.structures import Instances, Boxes
from detectron2.checkpoint import DetectionCheckpointer
from detectron2.modeling.anchor_generator import BufferList

/home/hinux/anaconda3/envs/38_04/lib/python3.8/site-packages/tqdm/auto.py:21: TqdmWarning: IProgress not found. Please update jupyter and ipywidgets. See https://ipywidgets.readthedocs.io/en/stable/user_install.html
  from .autonotebook import tqdm as notebook_tqdm


In [2]:

class Detectron2Model(nn.Module):
    MODEL_CONFIG = {
        "faster_rcnn": "COCO-Detection/faster_rcnn_R_50_FPN_3x.yaml",
        }

    def __init__(self, model_name):
        super().__init__()
        num_classes = 2
        pretrained = True
        nms_threshold = 0.5
        device = "cuda:0" if torch.cuda.is_available() else "cpu"

        self.cfg = get_cfg()
        config_path = self.MODEL_CONFIG[model_name]
        self.cfg.merge_from_file(model_zoo.get_config_file(config_path))

        # Update number of classes
        self.cfg.MODEL.ROI_HEADS.NUM_CLASSES = num_classes
        self.cfg.MODEL.RETINANET.NUM_CLASSES = num_classes
        # self.cfg.MODEL.ANCHOR_GENERATOR.NAME = "DenseBoxGenerator" #"DefaultAnchorGenerator"

        # Segmentation
        self.cfg.INPUT.MASK_FORMAT = 'bitmask'

        # NMS
        self.cfg.MODEL.ROI_HEADS.NMS_THRESH_TEST = nms_threshold
        self.cfg.MODEL.RPN.NMS_THRESH_TEST = nms_threshold

       
        self.cfg.MODEL.DEVICE = device
        model = build_model(self.cfg)

        # Load pretrained model
        if pretrained == False: # set it to False, since it has been training on 81 classes but we only have 2 classes
            DetectionCheckpointer(model).load(
                model_zoo.get_checkpoint_url(config_path))

        self.model = model

        def forward(self, x):
            if self.training:
                with EventStorage() as storage:
                    out = self.model(x)
            else:
                self.model.train()
                with torch.no_grad(), EventStorage() as storage:
                    out = self.model(x)
                self.model.eval()
            return out

        def infer(self, x):
            with torch.no_grad():
                out = self.model(x)
            return out


In [3]:
class FasterRCNN(Detectron2Model):
    def __init__(self):
        super().__init__('faster_rcnn')



In [4]:
myModel = FasterRCNN()

In [5]:
print(myModel)

FasterRCNN(
  (model): GeneralizedRCNN(
    (backbone): FPN(
      (fpn_lateral2): Conv2d(256, 256, kernel_size=(1, 1), stride=(1, 1))
      (fpn_output2): Conv2d(256, 256, kernel_size=(3, 3), stride=(1, 1), padding=(1, 1))
      (fpn_lateral3): Conv2d(512, 256, kernel_size=(1, 1), stride=(1, 1))
      (fpn_output3): Conv2d(256, 256, kernel_size=(3, 3), stride=(1, 1), padding=(1, 1))
      (fpn_lateral4): Conv2d(1024, 256, kernel_size=(1, 1), stride=(1, 1))
      (fpn_output4): Conv2d(256, 256, kernel_size=(3, 3), stride=(1, 1), padding=(1, 1))
      (fpn_lateral5): Conv2d(2048, 256, kernel_size=(1, 1), stride=(1, 1))
      (fpn_output5): Conv2d(256, 256, kernel_size=(3, 3), stride=(1, 1), padding=(1, 1))
      (top_block): LastLevelMaxPool()
      (bottom_up): ResNet(
        (stem): BasicStem(
          (conv1): Conv2d(
            3, 64, kernel_size=(7, 7), stride=(2, 2), padding=(3, 3), bias=False
            (norm): FrozenBatchNorm2d(num_features=64, eps=1e-05)
          )
       

# Before loading the checkpoint in

In [6]:
for k, v in myModel.state_dict().items():
    print(k)
    print(v)

model.backbone.fpn_lateral2.weight
tensor([[[[ 0.0555]],

         [[-0.0442]],

         [[ 0.0200]],

         ...,

         [[-0.0991]],

         [[-0.0394]],

         [[-0.0690]]],


        [[[ 0.0764]],

         [[-0.0606]],

         [[ 0.0994]],

         ...,

         [[ 0.0659]],

         [[-0.0953]],

         [[-0.0879]]],


        [[[-0.0291]],

         [[ 0.0151]],

         [[ 0.0215]],

         ...,

         [[-0.0366]],

         [[ 0.0494]],

         [[ 0.0384]]],


        ...,


        [[[ 0.0930]],

         [[-0.0679]],

         [[-0.0608]],

         ...,

         [[-0.0378]],

         [[-0.1077]],

         [[-0.0519]]],


        [[[-0.0949]],

         [[-0.0177]],

         [[-0.0219]],

         ...,

         [[-0.0219]],

         [[ 0.0459]],

         [[ 0.0866]]],


        [[[ 0.0325]],

         [[ 0.1073]],

         [[ 0.0331]],

         ...,

         [[-0.0013]],

         [[ 0.1036]],

         [[-0.0676]]]], device='cuda:0')
mode

In [7]:
for i in myModel.parameters(): # this is important since this example shows the "requires_grad=True"
    print(i)

Parameter containing:
tensor([[[[ 0.0555]],

         [[-0.0442]],

         [[ 0.0200]],

         ...,

         [[-0.0991]],

         [[-0.0394]],

         [[-0.0690]]],


        [[[ 0.0764]],

         [[-0.0606]],

         [[ 0.0994]],

         ...,

         [[ 0.0659]],

         [[-0.0953]],

         [[-0.0879]]],


        [[[-0.0291]],

         [[ 0.0151]],

         [[ 0.0215]],

         ...,

         [[-0.0366]],

         [[ 0.0494]],

         [[ 0.0384]]],


        ...,


        [[[ 0.0930]],

         [[-0.0679]],

         [[-0.0608]],

         ...,

         [[-0.0378]],

         [[-0.1077]],

         [[-0.0519]]],


        [[[-0.0949]],

         [[-0.0177]],

         [[-0.0219]],

         ...,

         [[-0.0219]],

         [[ 0.0459]],

         [[ 0.0866]]],


        [[[ 0.0325]],

         [[ 0.1073]],

         [[ 0.0331]],

         ...,

         [[-0.0013]],

         [[ 0.1036]],

         [[-0.0676]]]], device='cuda:0', requires_grad=Tru

# Checkpoint

In [8]:
# from collections import OrderedDict
# 
# checkpoint = torch.load("best.ckpt", map_location='cuda:0')
# 
# # this code is important for loading the state_dict correctly
# # from collections import OrderedDict
# # 
# new_state_dict = OrderedDict()
# 
# for k, v in checkpoint["state_dict"].items():
#     name = k[6:] # remove `module.`
#     new_state_dict[name] = v
# 
# checkpoint["state_dict"] = new_state_dict
# 
# myModel.load_state_dict(checkpoint["state_dict"])

# Freezing layers after loading checkpoint

In [9]:
for name, param in myModel.named_parameters():
    if "backbone" in name:
        param.requires_grad = False
    else:
        param.requires_grad = True
        

In [10]:
for name, param in myModel.named_parameters():
    print(f"Parameter: {name}, Requires Grad: {param.requires_grad}")

Parameter: model.backbone.fpn_lateral2.weight, Requires Grad: False
Parameter: model.backbone.fpn_lateral2.bias, Requires Grad: False
Parameter: model.backbone.fpn_output2.weight, Requires Grad: False
Parameter: model.backbone.fpn_output2.bias, Requires Grad: False
Parameter: model.backbone.fpn_lateral3.weight, Requires Grad: False
Parameter: model.backbone.fpn_lateral3.bias, Requires Grad: False
Parameter: model.backbone.fpn_output3.weight, Requires Grad: False
Parameter: model.backbone.fpn_output3.bias, Requires Grad: False
Parameter: model.backbone.fpn_lateral4.weight, Requires Grad: False
Parameter: model.backbone.fpn_lateral4.bias, Requires Grad: False
Parameter: model.backbone.fpn_output4.weight, Requires Grad: False
Parameter: model.backbone.fpn_output4.bias, Requires Grad: False
Parameter: model.backbone.fpn_lateral5.weight, Requires Grad: False
Parameter: model.backbone.fpn_lateral5.bias, Requires Grad: False
Parameter: model.backbone.fpn_output5.weight, Requires Grad: False
P

In [11]:
for i in myModel.parameters(): # this is important since this example shows the "requires_grad=True"
    print(i)

Parameter containing:
tensor([[[[ 0.0555]],

         [[-0.0442]],

         [[ 0.0200]],

         ...,

         [[-0.0991]],

         [[-0.0394]],

         [[-0.0690]]],


        [[[ 0.0764]],

         [[-0.0606]],

         [[ 0.0994]],

         ...,

         [[ 0.0659]],

         [[-0.0953]],

         [[-0.0879]]],


        [[[-0.0291]],

         [[ 0.0151]],

         [[ 0.0215]],

         ...,

         [[-0.0366]],

         [[ 0.0494]],

         [[ 0.0384]]],


        ...,


        [[[ 0.0930]],

         [[-0.0679]],

         [[-0.0608]],

         ...,

         [[-0.0378]],

         [[-0.1077]],

         [[-0.0519]]],


        [[[-0.0949]],

         [[-0.0177]],

         [[-0.0219]],

         ...,

         [[-0.0219]],

         [[ 0.0459]],

         [[ 0.0866]]],


        [[[ 0.0325]],

         [[ 0.1073]],

         [[ 0.0331]],

         ...,

         [[-0.0013]],

         [[ 0.1036]],

         [[-0.0676]]]], device='cuda:0')
Parameter contain

# Printing the shapes before loading the checkpoint in

In [12]:
for k, v in myModel.state_dict().items():
    print(k)
    print(v.shape)

model.backbone.fpn_lateral2.weight
torch.Size([256, 256, 1, 1])
model.backbone.fpn_lateral2.bias
torch.Size([256])
model.backbone.fpn_output2.weight
torch.Size([256, 256, 3, 3])
model.backbone.fpn_output2.bias
torch.Size([256])
model.backbone.fpn_lateral3.weight
torch.Size([256, 512, 1, 1])
model.backbone.fpn_lateral3.bias
torch.Size([256])
model.backbone.fpn_output3.weight
torch.Size([256, 256, 3, 3])
model.backbone.fpn_output3.bias
torch.Size([256])
model.backbone.fpn_lateral4.weight
torch.Size([256, 1024, 1, 1])
model.backbone.fpn_lateral4.bias
torch.Size([256])
model.backbone.fpn_output4.weight
torch.Size([256, 256, 3, 3])
model.backbone.fpn_output4.bias
torch.Size([256])
model.backbone.fpn_lateral5.weight
torch.Size([256, 2048, 1, 1])
model.backbone.fpn_lateral5.bias
torch.Size([256])
model.backbone.fpn_output5.weight
torch.Size([256, 256, 3, 3])
model.backbone.fpn_output5.bias
torch.Size([256])
model.backbone.bottom_up.stem.conv1.weight
torch.Size([64, 3, 7, 7])
model.backbone.bo

In [13]:
checkpoint = torch.load("best.ckpt", map_location='cuda:0')

In [14]:
# Do not use this code, 

# from collections import OrderedDict
# 
# new_state_dict = OrderedDict()
# 
# 
# for k, v in checkpoint["state_dict"].items():
#     six = 6
#     t = 48
#     name = k[6:] # remove `module.`
#     if name == "model.proposal_generator.anchor_generator.cell_anchors.0":
#         name = k[six:]
#         new_state_dict[name] = v
#     elif name == "model.proposal_generator.anchor_generator.cell_anchors.1":
#         name = k[six:]
#         new_state_dict[name] = v
#     elif name == "model.proposal_generator.anchor_generator.cell_anchors.2":
#         name = k[six:]
#         new_state_dict[name] = v
#     elif name == "model.proposal_generator.anchor_generator.cell_anchors.3":
#         name = k[six:]
#         new_state_dict[name] = v
#     elif name == "model.proposal_generator.anchor_generator.cell_anchors.4":
#         name = k[six:]
#         new_state_dict[name] = v
#     else:
#         new_state_dict[name] = v
#         
# checkpoint["state_dict"] = new_state_dict

In [15]:
# this code is important for loading the state_dict correctly
from collections import OrderedDict

new_state_dict = OrderedDict()

for k, v in checkpoint["state_dict"].items():
    name = k[6:] # remove `module.`
    new_state_dict[name] = v

checkpoint["state_dict"] = new_state_dict

# Printing the modified checkpoint

In [16]:
checkpoint["state_dict"]

OrderedDict([('model.backbone.fpn_lateral2.weight',
              tensor([[[[ 0.0030]],
              
                       [[ 0.0114]],
              
                       [[-0.0126]],
              
                       ...,
              
                       [[-0.0315]],
              
                       [[-0.0077]],
              
                       [[ 0.0047]]],
              
              
                      [[[-0.0127]],
              
                       [[ 0.0040]],
              
                       [[-0.0039]],
              
                       ...,
              
                       [[-0.0032]],
              
                       [[ 0.0124]],
              
                       [[-0.0160]]],
              
              
                      [[[-0.0019]],
              
                       [[ 0.0036]],
              
                       [[-0.0031]],
              
                       ...,
              
                      

In [17]:
myModel.load_state_dict(checkpoint["state_dict"])

<All keys matched successfully>

# State_dict after loading the checkpoint

In [18]:
print(myModel.state_dict())

OrderedDict([('model.backbone.fpn_lateral2.weight', tensor([[[[ 0.0030]],

         [[ 0.0114]],

         [[-0.0126]],

         ...,

         [[-0.0315]],

         [[-0.0077]],

         [[ 0.0047]]],


        [[[-0.0127]],

         [[ 0.0040]],

         [[-0.0039]],

         ...,

         [[-0.0032]],

         [[ 0.0124]],

         [[-0.0160]]],


        [[[-0.0019]],

         [[ 0.0036]],

         [[-0.0031]],

         ...,

         [[-0.0032]],

         [[-0.0106]],

         [[-0.0154]]],


        ...,


        [[[-0.0238]],

         [[ 0.0057]],

         [[ 0.0004]],

         ...,

         [[ 0.0073]],

         [[ 0.0116]],

         [[ 0.0046]]],


        [[[-0.0179]],

         [[ 0.0078]],

         [[ 0.0092]],

         ...,

         [[-0.0141]],

         [[ 0.0302]],

         [[-0.0050]]],


        [[[-0.0366]],

         [[-0.0124]],

         [[ 0.0001]],

         ...,

         [[ 0.0106]],

         [[ 0.0095]],

         [[-0.0008]]]], devi

In [19]:
print(myModel)

FasterRCNN(
  (model): GeneralizedRCNN(
    (backbone): FPN(
      (fpn_lateral2): Conv2d(256, 256, kernel_size=(1, 1), stride=(1, 1))
      (fpn_output2): Conv2d(256, 256, kernel_size=(3, 3), stride=(1, 1), padding=(1, 1))
      (fpn_lateral3): Conv2d(512, 256, kernel_size=(1, 1), stride=(1, 1))
      (fpn_output3): Conv2d(256, 256, kernel_size=(3, 3), stride=(1, 1), padding=(1, 1))
      (fpn_lateral4): Conv2d(1024, 256, kernel_size=(1, 1), stride=(1, 1))
      (fpn_output4): Conv2d(256, 256, kernel_size=(3, 3), stride=(1, 1), padding=(1, 1))
      (fpn_lateral5): Conv2d(2048, 256, kernel_size=(1, 1), stride=(1, 1))
      (fpn_output5): Conv2d(256, 256, kernel_size=(3, 3), stride=(1, 1), padding=(1, 1))
      (top_block): LastLevelMaxPool()
      (bottom_up): ResNet(
        (stem): BasicStem(
          (conv1): Conv2d(
            3, 64, kernel_size=(7, 7), stride=(2, 2), padding=(3, 3), bias=False
            (norm): FrozenBatchNorm2d(num_features=64, eps=1e-05)
          )
       

In [20]:
for i in myModel.parameters(): # this is important since this example shows the "requires_grad=True"
    print(i)

Parameter containing:
tensor([[[[ 0.0030]],

         [[ 0.0114]],

         [[-0.0126]],

         ...,

         [[-0.0315]],

         [[-0.0077]],

         [[ 0.0047]]],


        [[[-0.0127]],

         [[ 0.0040]],

         [[-0.0039]],

         ...,

         [[-0.0032]],

         [[ 0.0124]],

         [[-0.0160]]],


        [[[-0.0019]],

         [[ 0.0036]],

         [[-0.0031]],

         ...,

         [[-0.0032]],

         [[-0.0106]],

         [[-0.0154]]],


        ...,


        [[[-0.0238]],

         [[ 0.0057]],

         [[ 0.0004]],

         ...,

         [[ 0.0073]],

         [[ 0.0116]],

         [[ 0.0046]]],


        [[[-0.0179]],

         [[ 0.0078]],

         [[ 0.0092]],

         ...,

         [[-0.0141]],

         [[ 0.0302]],

         [[-0.0050]]],


        [[[-0.0366]],

         [[-0.0124]],

         [[ 0.0001]],

         ...,

         [[ 0.0106]],

         [[ 0.0095]],

         [[-0.0008]]]], device='cuda:0')
Parameter contain

In [21]:
for name, param in myModel.named_parameters():
    if "backbone" in name:
        param.requires_grad = False
    else:
        param.requires_grad = True

for name, param in myModel.named_parameters():
    print(f"Parameter: {name}, Requires Grad: {param.requires_grad}")

Parameter: model.backbone.fpn_lateral2.weight, Requires Grad: False
Parameter: model.backbone.fpn_lateral2.bias, Requires Grad: False
Parameter: model.backbone.fpn_output2.weight, Requires Grad: False
Parameter: model.backbone.fpn_output2.bias, Requires Grad: False
Parameter: model.backbone.fpn_lateral3.weight, Requires Grad: False
Parameter: model.backbone.fpn_lateral3.bias, Requires Grad: False
Parameter: model.backbone.fpn_output3.weight, Requires Grad: False
Parameter: model.backbone.fpn_output3.bias, Requires Grad: False
Parameter: model.backbone.fpn_lateral4.weight, Requires Grad: False
Parameter: model.backbone.fpn_lateral4.bias, Requires Grad: False
Parameter: model.backbone.fpn_output4.weight, Requires Grad: False
Parameter: model.backbone.fpn_output4.bias, Requires Grad: False
Parameter: model.backbone.fpn_lateral5.weight, Requires Grad: False
Parameter: model.backbone.fpn_lateral5.bias, Requires Grad: False
Parameter: model.backbone.fpn_output5.weight, Requires Grad: False
P

In [22]:
for i in myModel.parameters(): # this is important since this example shows the "requires_grad=True"
    print(i)

Parameter containing:
tensor([[[[ 0.0030]],

         [[ 0.0114]],

         [[-0.0126]],

         ...,

         [[-0.0315]],

         [[-0.0077]],

         [[ 0.0047]]],


        [[[-0.0127]],

         [[ 0.0040]],

         [[-0.0039]],

         ...,

         [[-0.0032]],

         [[ 0.0124]],

         [[-0.0160]]],


        [[[-0.0019]],

         [[ 0.0036]],

         [[-0.0031]],

         ...,

         [[-0.0032]],

         [[-0.0106]],

         [[-0.0154]]],


        ...,


        [[[-0.0238]],

         [[ 0.0057]],

         [[ 0.0004]],

         ...,

         [[ 0.0073]],

         [[ 0.0116]],

         [[ 0.0046]]],


        [[[-0.0179]],

         [[ 0.0078]],

         [[ 0.0092]],

         ...,

         [[-0.0141]],

         [[ 0.0302]],

         [[-0.0050]]],


        [[[-0.0366]],

         [[-0.0124]],

         [[ 0.0001]],

         ...,

         [[ 0.0106]],

         [[ 0.0095]],

         [[-0.0008]]]], device='cuda:0')
Parameter contain

In [23]:
print(myModel.state_dict())

OrderedDict([('model.backbone.fpn_lateral2.weight', tensor([[[[ 0.0030]],

         [[ 0.0114]],

         [[-0.0126]],

         ...,

         [[-0.0315]],

         [[-0.0077]],

         [[ 0.0047]]],


        [[[-0.0127]],

         [[ 0.0040]],

         [[-0.0039]],

         ...,

         [[-0.0032]],

         [[ 0.0124]],

         [[-0.0160]]],


        [[[-0.0019]],

         [[ 0.0036]],

         [[-0.0031]],

         ...,

         [[-0.0032]],

         [[-0.0106]],

         [[-0.0154]]],


        ...,


        [[[-0.0238]],

         [[ 0.0057]],

         [[ 0.0004]],

         ...,

         [[ 0.0073]],

         [[ 0.0116]],

         [[ 0.0046]]],


        [[[-0.0179]],

         [[ 0.0078]],

         [[ 0.0092]],

         ...,

         [[-0.0141]],

         [[ 0.0302]],

         [[-0.0050]]],


        [[[-0.0366]],

         [[-0.0124]],

         [[ 0.0001]],

         ...,

         [[ 0.0106]],

         [[ 0.0095]],

         [[-0.0008]]]], devi

# Printing the shapes after loading the checkpoint in

In [24]:
for k, v in myModel.state_dict().items():
    print(k)
    print(v.shape)

model.backbone.fpn_lateral2.weight
torch.Size([256, 256, 1, 1])
model.backbone.fpn_lateral2.bias
torch.Size([256])
model.backbone.fpn_output2.weight
torch.Size([256, 256, 3, 3])
model.backbone.fpn_output2.bias
torch.Size([256])
model.backbone.fpn_lateral3.weight
torch.Size([256, 512, 1, 1])
model.backbone.fpn_lateral3.bias
torch.Size([256])
model.backbone.fpn_output3.weight
torch.Size([256, 256, 3, 3])
model.backbone.fpn_output3.bias
torch.Size([256])
model.backbone.fpn_lateral4.weight
torch.Size([256, 1024, 1, 1])
model.backbone.fpn_lateral4.bias
torch.Size([256])
model.backbone.fpn_output4.weight
torch.Size([256, 256, 3, 3])
model.backbone.fpn_output4.bias
torch.Size([256])
model.backbone.fpn_lateral5.weight
torch.Size([256, 2048, 1, 1])
model.backbone.fpn_lateral5.bias
torch.Size([256])
model.backbone.fpn_output5.weight
torch.Size([256, 256, 3, 3])
model.backbone.fpn_output5.bias
torch.Size([256])
model.backbone.bottom_up.stem.conv1.weight
torch.Size([64, 3, 7, 7])
model.backbone.bo

# After loading the checkpoint in

In [25]:
for k, v in myModel.state_dict().items():
    print(k)
    print(v)

model.backbone.fpn_lateral2.weight
tensor([[[[ 0.0030]],

         [[ 0.0114]],

         [[-0.0126]],

         ...,

         [[-0.0315]],

         [[-0.0077]],

         [[ 0.0047]]],


        [[[-0.0127]],

         [[ 0.0040]],

         [[-0.0039]],

         ...,

         [[-0.0032]],

         [[ 0.0124]],

         [[-0.0160]]],


        [[[-0.0019]],

         [[ 0.0036]],

         [[-0.0031]],

         ...,

         [[-0.0032]],

         [[-0.0106]],

         [[-0.0154]]],


        ...,


        [[[-0.0238]],

         [[ 0.0057]],

         [[ 0.0004]],

         ...,

         [[ 0.0073]],

         [[ 0.0116]],

         [[ 0.0046]]],


        [[[-0.0179]],

         [[ 0.0078]],

         [[ 0.0092]],

         ...,

         [[-0.0141]],

         [[ 0.0302]],

         [[-0.0050]]],


        [[[-0.0366]],

         [[-0.0124]],

         [[ 0.0001]],

         ...,

         [[ 0.0106]],

         [[ 0.0095]],

         [[-0.0008]]]], device='cuda:0')
mode

# comparing the best.cpkt with the newest checkpoint

In [26]:
new_checkpoint = torch.load("myTrain.ckpt", map_location='cuda:0')

In [27]:
new_checkpoint["state_dict"]

OrderedDict([('model.model.backbone.fpn_lateral2.weight',
              tensor([[[[ 0.0030]],
              
                       [[ 0.0114]],
              
                       [[-0.0126]],
              
                       ...,
              
                       [[-0.0315]],
              
                       [[-0.0077]],
              
                       [[ 0.0047]]],
              
              
                      [[[-0.0127]],
              
                       [[ 0.0040]],
              
                       [[-0.0039]],
              
                       ...,
              
                       [[-0.0032]],
              
                       [[ 0.0124]],
              
                       [[-0.0160]]],
              
              
                      [[[-0.0019]],
              
                       [[ 0.0036]],
              
                       [[-0.0031]],
              
                       ...,
              
                

In [ ]:
new_checkpoint.named_parameters()

In [29]:
from pytorch_lightning.callbacks import ModelCheckpoint
checkpoint_callback = ModelCheckpoint(dirpath='best.ckpt')

In [36]:
print(checkpoint_callback.best_k_models)

{}
